# With PyTorch

In [1]:
import os
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
from torch.utils.data import DataLoader, TensorDataset
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler

04/21=The following until train_test_split cell
Is testing a new data structure for easier feeding
into any network, while keeping the time-based
TDS spectral data intact. 


In [2]:
#Load and preprocess the data
folder_path = '1kfiles'
data = {}

for filename in os.listdir(folder_path):
    file_path = os.path.join(folder_path, filename)
    if os.path.isfile(file_path):
        with open(file_path, 'r') as file:
            df1 = pd.read_csv(file_path, header=None, names=['des_flux', 'detrap_en', 'def_conc'], index_col=None, squeeze = True)
            data[filename] = df1
            
# Combine all the data into a single dataframe
df = pd.concat(data.values())

# Drop NaN values
#df = df.dropna()

display(df)

C:\Users\yayy_\AppData\Local\Temp\ipykernel_34116\3278440441.py:9: FutureWarning: The squeeze argument has been deprecated and will be removed in a future version. Append .squeeze("columns") to the call to squeeze.


  df1 = pd.read_csv(file_path, header=None, names=['des_flux', 'detrap_en', 'def_conc'], index_col=None, squeeze = True)
C:\Users\yayy_\AppData\Local\Temp\ipykernel_34116\3278440441.py:9: FutureWarning: The squeeze argument has been deprecated and will be removed in a future version. Append .squeeze("columns") to the call to squeeze.


  df1 = pd.read_csv(file_path, header=None, names=['des_flux', 'detrap_en', 'def_conc'], index_col=None, squeeze = True)
C:\Users\yayy_\AppData\Local\Temp\ipykernel_34116\3278440441.py:9: FutureWarning: The squeeze argument has been deprecated and will be removed in a future version. Append .squeeze("columns") to the call to squeeze.


  df1 = pd.read_csv(file_path, header=None, names=['des_flux', 'detrap_en', 'def_conc'], index_col=None, sq

des_flux  detrap_en  def_conc
0    1.269745e-10   1.051587  0.011064
1    8.488521e+14   1.185898  0.006066
2    1.239766e+15   1.203310  0.020460
3    1.784721e+15   1.242848  0.005844
4    2.528399e+15        NaN       NaN
..            ...        ...       ...
296  7.160074e+07        NaN       NaN
297 -6.944291e+08        NaN       NaN
298 -5.921441e+08        NaN       NaN
299 -1.240336e+09        NaN       NaN
300  1.267471e+10        NaN       NaN

[301000 rows x 3 columns]

In [16]:
#Take each data feature and reshape for 
#the first axis to be equal to number of files
#fed in. In this case, 500. This makes feeding into
#train test splits and networks much easier. 

#Maybe turn this into a loop?
des_flux=df['des_flux']
des_flux=des_flux.tolist()
num_files=int(len(des_flux)/301)
des_flux=np.reshape(des_flux, [num_files, 301])
display(des_flux)
print(type(des_flux[0]), des_flux.shape)

detrap_en=df['detrap_en']
detrap_en=detrap_en.dropna()
detrap_en=detrap_en.tolist()
num_files=int(len(detrap_en)/4)
detrap_en=np.reshape(detrap_en, [num_files, 4])
print(detrap_en, detrap_en.shape)

def_conc=df['def_conc']
def_conc=def_conc.dropna()
def_conc=def_conc.tolist()
num_files=int(len(def_conc)/4)
def_conc=np.reshape(def_conc, [num_files, 4])
print(def_conc, def_conc.shape)

array([[ 1.26974494e-10,  8.48852054e+14,  1.23976624e+15, ...,
        -5.06243457e+11,  1.48607468e+12, -2.00064455e+13],
       [ 0.00000000e+00,  4.75905724e+11,  7.63578326e+11, ...,
        -2.54585985e+10, -4.33822251e+10, -6.32853530e+10],
       [ 0.00000000e+00,  4.90315082e+11,  7.87398576e+11, ...,
         3.05676224e+10,  4.94117204e+10, -6.94978103e+10],
       ...,
       [-1.61113135e-09,  5.30994094e+15,  7.24433559e+15, ...,
        -2.83191940e+11, -2.97233202e+11,  3.12348951e+11],
       [ 0.00000000e+00,  2.09801065e+15,  2.98570846e+15, ...,
         5.66148036e+13,  2.69771268e+13,  1.17249939e+13],
       [ 0.00000000e+00,  3.82317650e+15,  5.08373506e+15, ...,
        -5.92144090e+08, -1.24033587e+09,  1.26747148e+10]])

<class 'numpy.ndarray'> (1000, 301)
[[1.05158736 1.1858984  1.20331037 1.24284827]
 [1.25596152 1.5426616  1.63994921 1.86117181]
 [1.25822251 1.45758869 1.51721682 1.66222764]
 ...
 [1.01457836 1.53773973 1.54031238 1.78321747]
 [1.03144402 1.35668867 1.72645702 1.99768237]
 [1.00074039 1.27513497 1.35716673 1.38739602]] (1000, 4)
[[0.01106389 0.00606641 0.02045982 0.00584418]
 [0.01107136 0.00256641 0.00625459 0.00236498]
 [0.01906223 0.0150854  0.00796364 0.01020889]
 ...
 [0.02252724 0.0228933  0.00363031 0.02132085]
 [0.01466683 0.00754141 0.01496606 0.01868682]
 [0.00514325 0.00146842 0.00609607 0.00689274]] (1000, 4)


In [17]:
#Concatenates the output dataset, creating a 2d array
#of (file, array of detrap_en + def_conc)
#Tried a 3d array of (file, value column, # of values)
#but PyTorch and Tensorflow gave size issues

def_param = np.concatenate([detrap_en, def_conc], axis=1)
print(def_param.shape)

(1000, 8)


In [18]:
# Split the data into train and test sets
X_train, X_test= train_test_split(des_flux, test_size=0.1, random_state=42)
y_train, y_test = train_test_split(def_param, test_size=0.1, random_state=42)
display(X_train.shape, X_test.shape, y_train.shape, y_test.shape)

(900, 301)

(100, 301)

(900, 8)

(100, 8)

In [19]:
# Normalize the data
scaler = StandardScaler(with_mean=True, with_std=True)
X_train_norm = scaler.fit_transform(X_train.reshape(-1, 1))
X_test_norm = scaler.transform(X_test.reshape(-1, 1))

In [20]:
print(X_train_norm.mean(), X_train_norm.std(), X_train_norm.min(), X_train_norm.max())
print(X_test_norm.mean(), X_test_norm.std(), X_test_norm.min(), X_test_norm.max())

#Save the values for later use? Necessary or no?
X_train_mean, X_train_std = X_train_norm.mean(), X_train_norm.std()
X_test_mean, X_test_std = X_test_norm.mean(), X_test_norm.std()

-6.3185583257515e-17 0.9999999999999999 -0.8448064194115795 5.423215888476747
0.028211859599414576 1.0354345174789334 -0.8439433601115015 4.384811515864618


In [21]:
#Reshape data for model input
#Checked to make sure the time-series nature of
#the X_train, X_test is intact, can double check
#By calling an array and comparing with a .csv file
X_train_transform = np.reshape(X_train_norm, (X_train.shape))
print(X_train_transform.shape)

X_test_transform = np.reshape(X_test_norm, (X_test.shape))
print(X_test_transform.shape)

(900, 301)
(100, 301)


In [22]:
# Convert data to PyTorch tensors
X_train_transform = torch.tensor(X_train_transform, dtype=torch.float32)
X_test_transform = torch.tensor(X_test_transform, dtype=torch.float32)
y_train = torch.tensor(y_train, dtype=torch.float32)
y_test = torch.tensor(y_test, dtype=torch.float32)

print(type(X_train_transform), type(X_train_transform), type(y_train), type(y_test))

<class 'torch.Tensor'> <class 'torch.Tensor'> <class 'torch.Tensor'> <class 'torch.Tensor'>


In [10]:
print(X_train_transform.shape, X_test_transform.shape)
print(y_train.shape, y_test.shape)

torch.Size([900, 301]) torch.Size([100, 301])
torch.Size([900, 8]) torch.Size([100, 8])


In [11]:
# Create a DataLoader for the training and test sets
train_dataset = TensorDataset(X_train_transform, y_train)
train_loader = DataLoader(train_dataset, batch_size=32, shuffle=True)
test_dataset = TensorDataset(X_test_transform, y_test)
test_loader = DataLoader(test_dataset, batch_size=32)

In [12]:
#Getting the same error as Mai, some value is being converted
#from a tensor to tuple and the evaluate methods don't like it
#but the model runs.

# Define the neural network model
class FeedforwardNN(nn.Module):
    def __init__(self):
        super(FeedforwardNN, self).__init__()
        self.fc1 = nn.Linear(301, 64)
        self.fc2 = nn.Linear(64, 32)
        self.fc3 = nn.Linear(32, 8)
        self.relu = nn.ReLU()
        self.dropout = nn.Dropout(p=0.5)
        
    def forward(self, x):
        x = self.relu(self.fc1(x))
        x = self.dropout(x)
        x = self.relu(self.fc2(x))
        x = self.dropout(x)
        x = self.fc3(x)
        return x

# Initialize the model and optimizer
model = FeedforwardNN()
criterion = nn.MSELoss()
optimizer = torch.optim.Adam(model.parameters(), lr=0.001)

# Train the model
num_epochs = 100
for epoch in range(num_epochs):
    for i, (inputs, targets) in enumerate(train_loader):
        optimizer.zero_grad()
        outputs = model(inputs)
        loss = criterion(outputs, targets)
        loss.backward()
        optimizer.step()

    if epoch % 10 == 0:
        print(f'Epoch [{epoch}/{num_epochs}], Loss: {loss.item():.4f}')

# Evaluate the neural network on the test data
model.eval()
with torch.no_grad():
    outputs = model(test_dataset[:, [0]])
    loss = criterion(outputs, test_dataset[:, 1:])
    print('Test Loss: {:.4f}'.format(loss.item()))


Epoch [0/100], Loss: 0.5149
Epoch [10/100], Loss: 0.0537
Epoch [20/100], Loss: 0.0919
Epoch [30/100], Loss: 0.0374
Epoch [40/100], Loss: 0.0400
Epoch [50/100], Loss: 0.0367
Epoch [60/100], Loss: 0.0395
Epoch [70/100], Loss: 0.0178
Epoch [80/100], Loss: 0.0547
Epoch [90/100], Loss: 0.0157


TypeError: linear(): argument 'input' (position 1) must be Tensor, not tuple

# TensorFlow

In [3]:
import os
import pandas as pd
import numpy as np
import tensorflow as tf
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler

# Set random seed for reproducibility
tf.random.set_seed(42)

#Load and preprocess the data
folder_path = 'TDS_data_15000'
data = {}

for filename in os.listdir(folder_path):
    file_path = os.path.join(folder_path, filename)
    if os.path.isfile(file_path):
        with open(file_path, 'r') as file:
            df1 = pd.read_csv(file_path, header=None, names=['des_flux', 'detrap_en', 'def_conc'], index_col=None, squeeze = True)
            data[filename] = df1
            
# Combine all the data into a single dataframe
df = pd.concat(data.values())

C:\Users\2018m\AppData\Local\Temp\ipykernel_3456\4237015266.py:19: FutureWarning: The squeeze argument has been deprecated and will be removed in a future version. Append .squeeze("columns") to the call to squeeze.


  df1 = pd.read_csv(file_path, header=None, names=['des_flux', 'detrap_en', 'def_conc'], index_col=None, squeeze = True)
C:\Users\2018m\AppData\Local\Temp\ipykernel_3456\4237015266.py:19: FutureWarning: The squeeze argument has been deprecated and will be removed in a future version. Append .squeeze("columns") to the call to squeeze.


  df1 = pd.read_csv(file_path, header=None, names=['des_flux', 'detrap_en', 'def_conc'], index_col=None, squeeze = True)
C:\Users\2018m\AppData\Local\Temp\ipykernel_3456\4237015266.py:19: FutureWarning: The squeeze argument has been deprecated and will be removed in a future version. Append .squeeze("columns") to the call to squeeze.


  df1 = pd.read_csv(file_path, header=None, names=['des_flux', 'detrap_en', 'def_conc'], index_col=None, sq

In [4]:
#Take each data feature and reshape for 
#the first axis to be equal to number of files
#fed in. In this case, 500. This makes feeding into
#train test splits and networks much easier. 

#Maybe turn this into a loop?
des_flux=df['des_flux']
des_flux=des_flux.tolist()
num_files=int(len(des_flux)/301)
des_flux=np.reshape(des_flux, [num_files, 301])
display(des_flux)
#print(type(des_flux[0]), des_flux.shape)

detrap_en=df['detrap_en']
detrap_en=detrap_en.dropna()
detrap_en=detrap_en.tolist()
num_files=int(len(detrap_en)/4)
detrap_en=np.reshape(detrap_en, [num_files, 4])
#print(detrap_en, detrap_en.shape)

def_conc=df['def_conc']
def_conc=def_conc.dropna()
def_conc=def_conc.tolist()
num_files=int(len(def_conc)/4)
def_conc=np.reshape(def_conc, [num_files, 4])
#print(def_conc, def_conc.shape)

array([[ 0.00000000e+00,  5.43155589e+14,  8.07107134e+14, ...,
         2.01564589e+10,  9.74552070e+09, -8.88008277e+09],
       [ 0.00000000e+00,  2.59668597e+12,  4.07671353e+12, ...,
         1.60091558e+08,  3.88972048e+08,  6.25874398e+08],
       [ 0.00000000e+00,  3.33968287e+09,  5.64202057e+09, ...,
        -1.77104244e+11, -3.25368009e+11,  2.11390510e+11],
       ...,
       [-4.35153102e-10,  3.25823198e+15,  4.51811591e+15, ...,
        -4.40433457e+11, -2.05314378e+11, -1.19524462e+11],
       [ 0.00000000e+00,  1.58741825e+14,  2.39341911e+14, ...,
        -1.13773164e+10, -8.33057727e+09,  1.28537117e+08],
       [ 0.00000000e+00,  2.59323182e+14,  3.86532956e+14, ...,
        -1.18533990e+11, -1.75308845e+11,  2.22380273e+11]])

In [9]:
def_param = np.concatenate([detrap_en, def_conc], axis=1)

In [10]:
# Split the data into train and test sets
X_train, X_test= train_test_split(des_flux, test_size=0.1, random_state=42)
y_train, y_test = train_test_split(def_param, test_size=0.1, random_state=42)
display(X_train.shape, X_test.shape, y_train.shape, y_test.shape)

(13500, 301)

(1500, 301)

(13500, 8)

(1500, 8)

In [11]:
# Normalize the data
scaler = StandardScaler(with_mean=True, with_std=True)
X_train_norm = scaler.fit_transform(X_train.reshape(-1, 1))
X_test_norm = scaler.transform(X_test.reshape(-1, 1))

#Reshape data for model input
#Checked to make sure the time-series nature of
#the X_train, X_test is intact, can double check
#By calling an array and comparing with a .csv file
X_train_transform = np.reshape(X_train_norm, (X_train.shape))
print(X_train_transform.shape)

X_test_transform = np.reshape(X_test_norm, (X_test.shape))
print(X_test_transform.shape)

(13500, 301)
(1500, 301)


In [12]:
#TensorFlow runs as well now, just not well.
#Now we can optimize. 

# Define the model architecture
model = tf.keras.models.Sequential()
model.add(tf.keras.layers.Dense(units=64, activation='relu', 
                                    kernel_initializer=tf.keras.initializers.GlorotUniform()))
model.add(tf.keras.layers.Dense(units=32, activation='relu',
                                    kernel_initializer=tf.keras.initializers.GlorotUniform()))
model.add(tf.keras.layers.Dense(units=8, activation='softmax',
                                    kernel_initializer=tf.keras.initializers.GlorotUniform()))

# Compile the model
model.compile(optimizer=tf.optimizers.Adam(learning_rate=0.1), loss='mse')

# Train the model
history = model.fit(X_train_transform, y_train, epochs=10, validation_split=0.1)

# Evaluate the model on the test set
test_loss = model.evaluate(X_test_transform, y_test)
print(f'Test loss: {test_loss:.4f}')


Epoch 1/10
380/380 [==============================] - 2s 3ms/step - loss: 0.8921 - val_loss: 0.8866
Epoch 2/10
380/380 [==============================] - 1s 2ms/step - loss: 0.8922 - val_loss: 0.8866
Epoch 3/10
380/380 [==============================] - 1s 2ms/step - loss: 0.8922 - val_loss: 0.8866
Epoch 4/10
380/380 [==============================] - 1s 2ms/step - loss: 0.8922 - val_loss: 0.8866
Epoch 5/10
380/380 [==============================] - 1s 2ms/step - loss: 0.8922 - val_loss: 0.8866
Epoch 6/10
380/380 [==============================] - 1s 2ms/step - loss: 0.8922 - val_loss: 0.8866
Epoch 7/10
380/380 [==============================] - 1s 2ms/step - loss: 0.8922 - val_loss: 0.8866
Epoch 8/10
380/380 [==============================] - 1s 2ms/step - loss: 0.8922 - val_loss: 0.8866
Epoch 9/10
380/380 [==============================] - 1s 2ms/step - loss: 0.8922 - val_loss: 0.8866
Epoch 10/10
47/47 [==============================] - 0s 2ms/step - loss: 0.8966
Test loss: 0.8966
